In [ ]:
import cv2
import time
import numpy as np
from google.colab import files

# ------------------------------
# Configuration
# ------------------------------
VIDEO_PATH = "/content/WIN_20251107_17_20_03_Pro.mp4"
OUTPUT_PATH = "/content/edge_output.mp4"
FRAME_WIDTH = 640
FRAME_HEIGHT = 480

# store previous frame for temporal smoothing
prev_fused = None


# ------------------------------
# Utility Functions
# ------------------------------
def resize_frame(frame, width, height):
    return cv2.resize(frame, (width, height), interpolation=cv2.INTER_AREA)


def to_grayscale(frame):
    return cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)


def apply_clahe(gray):
    clahe = cv2.createCLAHE(clipLimit=2.0, tileGridSize=(8, 8))
    return clahe.apply(gray)


def bilateral_smooth(gray):
    return cv2.bilateralFilter(gray, 9, 75, 75)


def dynamic_canny(gray):
    sigma = np.std(gray)
    lower = max(20, int(0.66 * sigma))
    upper = min(200, int(1.33 * sigma))
    return cv2.Canny(gray, lower, upper)


def laplacian_edge(gray):
    lap = cv2.Laplacian(gray, cv2.CV_64F)
    return cv2.convertScaleAbs(lap)


def sobel_gradient(gray):
    sobelx = cv2.Sobel(gray, cv2.CV_64F, 1, 0)
    sobely = cv2.Sobel(gray, cv2.CV_64F, 0, 1)
    mag = np.sqrt(sobelx**2 + sobely**2)
    return cv2.convertScaleAbs(mag)


def fuse_edges(canny, lap, sobel):
    fused = cv2.addWeighted(canny, 0.6, lap, 0.3, 0)
    fused = cv2.addWeighted(fused, 0.7, sobel, 0.3, 0)
    return fused


def morphology_close(fused):
    kernel = np.ones((3, 3), np.uint8)
    return cv2.morphologyEx(fused, cv2.MORPH_CLOSE, kernel)


def temporal_smooth(fused):
    global prev_fused
    if prev_fused is None:
        prev_fused = fused.copy()
    fused = cv2.addWeighted(fused, 0.7, prev_fused, 0.3, 0)
    prev_fused = fused.copy()
    return fused


def overlay_edges(frame, fused):
    overlay = frame.copy()
    overlay[fused > 40] = [0, 0, 255]
    return overlay


# ------------------------------
# Main Processing Function
# ------------------------------
def process_frame(frame):
    gray = to_grayscale(frame)
    clahe_gray = apply_clahe(gray)
    smooth = bilateral_smooth(clahe_gray)
    canny = dynamic_canny(smooth)
    lap = laplacian_edge(smooth)
    sobel = sobel_gradient(smooth)
    fused = fuse_edges(canny, lap, sobel)
    fused = morphology_close(fused)
    fused = temporal_smooth(fused)
    output = overlay_edges(frame, fused)
    return output


# ------------------------------
# Open Video Stream
# ------------------------------
cap = cv2.VideoCapture(VIDEO_PATH)
if not cap.isOpened():
    raise IOError("Error: Could not open video file.")

fps = cap.get(cv2.CAP_PROP_FPS)
if fps == 0: fps = 30  # fallback

fourcc = cv2.VideoWriter_fourcc(*"mp4v")
out = cv2.VideoWriter(OUTPUT_PATH, fourcc, fps, (FRAME_WIDTH, FRAME_HEIGHT))

prev_time = time.time()
frame_counter = 0

# ------------------------------
# Processing Loop
# ------------------------------
while True:
    ret, frame = cap.read()
    if not ret:
        print("Finished processing video.")
        break

    frame = resize_frame(frame, FRAME_WIDTH, FRAME_HEIGHT)
    output = process_frame(frame)
    out.write(output)

    # FPS tracker
    frame_counter += 1
    curr_time = time.time()
    if curr_time - prev_time >= 1:
        fps_live = frame_counter / (curr_time - prev_time)
        print(f"Live FPS: {fps_live:.2f}")
        prev_time = curr_time
        frame_counter = 0


# ------------------------------
# Cleanup
# ------------------------------
cap.release()
out.release()
print(f"✅ Video saved at: {OUTPUT_PATH}")

files.download(OUTPUT_PATH)


Live FPS: 11.31
Live FPS: 14.39
Live FPS: 13.80
Live FPS: 13.28
Live FPS: 13.79
Live FPS: 14.28
Live FPS: 13.59
Live FPS: 13.97
Live FPS: 10.84
Live FPS: 7.87
Finished processing video.
✅ Video saved at: /content/edge_output.mp4


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>